In [47]:
train_file ='train/in.tsv.xz'
test_file = 'dev-0/in.tsv.xz'
out_file = 'dev-0/out.tsv'

In [25]:
from itertools import islice
import regex as re
import sys
from torchtext.vocab import build_vocab_from_iterator
import lzma
import pickle
import re
import torch
from torch import nn
from torch.utils.data import IterableDataset
import itertools
from torch.utils.data import DataLoader
import yaml

In [15]:
params = yaml.load(open('config/params.yaml'))

/tmp/ipykernel_5410/1074132307.py:1: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  params = yaml.load(open('config/params.yaml'))


In [26]:
params = {
'epochs': 3,
'embed_size': 256,
'device': 'cuda',
'vocab_size': 35000,
'batch_size': 3200,
'learning_rate': 0.001,
'k': 15, #top k words
'wildcard_minweight': 0.01,
'beta': 0.85
}

In [27]:
params

{'epochs': 3,
 'embed_size': 256,
 'device': 'cuda',
 'vocab_size': 35000,
 'batch_size': 3200,
 'learning_rate': 0.001,
 'k': 15,
 'wildcard_minweight': 0.01,
 'beta': 0.85}

In [28]:
def get_words_from_line(line):
    line = line.rstrip()
    yield '<s>'
    line = preprocess(line)
    for t in line.split(' '):
        yield t
    yield '</s>'


def get_word_lines_from_file(file_name):
    n = 0
    with lzma.open(file_name, 'r') as fh:
        for line in fh:
            n+=1
            if n%1000==0:
                print(n)
            yield get_words_from_line(line.decode('utf-8'))

###preprocessing
def preprocess(line):
    line = get_rid_of_header(line)
    line = replace_endline(line)
    return line

def get_rid_of_header(line):
    line = line.split('\t')[6:]
    return " ".join(line)
    
def replace_endline(line):
    line = line.replace("\\n", " ")
    return line

In [29]:
def look_ahead_iterator(gen):
    prev5 = None
    prev4 = None
    prev3 = None
    prev2 = None
    prev1 = None
    for item in gen:
        if None not in [prev5, prev4, prev3, prev2, prev1]:
            yield (prev5, prev4, prev3, prev2, prev1, item)
        prev5 = prev4
        prev4 = prev3
        prev3 = prev2
        prev2 = prev1
        prev1 = item

class Hexagrams(IterableDataset):
  def __init__(self, text_file, vocabulary_size):
      self.vocab = build_vocab_from_iterator(
         get_word_lines_from_file(text_file),
         max_tokens = vocabulary_size,
         specials = ['<unk>'])
      self.vocab.set_default_index(self.vocab['<unk>'])
      self.vocabulary_size = vocabulary_size
      self.text_file = text_file

  def __iter__(self):
     return look_ahead_iterator(
         (self.vocab[t] for t in itertools.chain.from_iterable(get_word_lines_from_file(self.text_file))))
    

In [30]:
with open('filename.pickle','rb') as handle:
    vocab = pickle.load(handle)

In [31]:
train_dataset = Hexagrams(train_file, params['vocab_size'])

1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000



KeyboardInterrupt



In [9]:
for item in train_dataset:
    print(item)

(31, 0, 0, 3910, 135, 0)
(0, 0, 3910, 135, 0, 0)
(0, 3910, 135, 0, 0, 0)
(3910, 135, 0, 0, 0, 1)
(135, 0, 0, 0, 1, 388)
(0, 0, 0, 1, 388, 2)
(0, 0, 1, 388, 2, 762)
(0, 1, 388, 2, 762, 0)
(1, 388, 2, 762, 0, 1)
(388, 2, 762, 0, 1, 195)
(2, 762, 0, 1, 195, 2)
(762, 0, 1, 195, 2, 2810)
(0, 1, 195, 2, 2810, 0)
(1, 195, 2, 2810, 0, 0)
(195, 2, 2810, 0, 0, 0)
(2, 2810, 0, 0, 0, 7)
(2810, 0, 0, 0, 7, 1)
(0, 0, 0, 7, 1, 146)
(0, 0, 7, 1, 146, 52)
(0, 7, 1, 146, 52, 47)
(7, 1, 146, 52, 47, 388)
(1, 146, 52, 47, 388, 0)
(146, 52, 47, 388, 0, 449)
(52, 47, 388, 0, 449, 35)
(47, 388, 0, 449, 35, 23166)
(388, 0, 449, 35, 23166, 251)
(0, 449, 35, 23166, 251, 5238)
(449, 35, 23166, 251, 5238, 24)
(35, 23166, 251, 5238, 24, 659)
(23166, 251, 5238, 24, 659, 0)
(251, 5238, 24, 659, 0, 8623)
(5238, 24, 659, 0, 8623, 3)
(24, 659, 0, 8623, 3, 5018)
(659, 0, 8623, 3, 5018, 35)
(0, 8623, 3, 5018, 35, 29)
(8623, 3, 5018, 35, 29, 54)
(3, 5018, 35, 29, 54, 11558)
(5018, 35, 29, 54, 11558, 0)
(35, 29, 54, 11558,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



(13, 44, 393, 0, 30, 31)
(44, 393, 0, 30, 31, 0)
(393, 0, 30, 31, 0, 0)
(0, 30, 31, 0, 0, 0)
(30, 31, 0, 0, 0, 217)
(31, 0, 0, 0, 217, 80)
(0, 0, 0, 217, 80, 26)
(0, 0, 217, 80, 26, 138)
(0, 217, 80, 26, 138, 1768)
(217, 80, 26, 138, 1768, 24111)
(80, 26, 138, 1768, 24111, 3)
(26, 138, 1768, 24111, 3, 27)
(138, 1768, 24111, 3, 27, 6204)
(1768, 24111, 3, 27, 6204, 144)
(24111, 3, 27, 6204, 144, 1433)
(3, 27, 6204, 144, 1433, 1155)
(27, 6204, 144, 1433, 1155, 3)
(6204, 144, 1433, 1155, 3, 0)
(144, 1433, 1155, 3, 0, 17)
(1433, 1155, 3, 0, 17, 0)
(1155, 3, 0, 17, 0, 0)
(3, 0, 17, 0, 0, 22413)
(0, 17, 0, 0, 22413, 0)
(17, 0, 0, 22413, 0, 29819)
(0, 0, 22413, 0, 29819, 0)
(0, 22413, 0, 29819, 0, 0)
(22413, 0, 29819, 0, 0, 10831)
(0, 29819, 0, 0, 10831, 0)
(29819, 0, 0, 10831, 0, 16032)
(0, 0, 10831, 0, 16032, 0)
(0, 10831, 0, 16032, 0, 0)
(10831, 0, 16032, 0, 0, 3)
(0, 16032, 0, 0, 3, 0)
(16032, 0, 0, 3, 0, 72)
(0, 0, 3, 0, 72, 3)
(0, 3, 0, 72, 3, 145)
(3, 0, 72, 3, 145, 17)
(0, 72, 3, 145, 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



KeyboardInterrupt: 

In [32]:
class BoW_position_HexagramNeuralLanguageModel(nn.Module):
    def __init__(self, vocabulary_size, embedding_size, beta_factor):
        super(BoW_position_HexagramNeuralLanguageModel, self).__init__()
        self.embeddings = nn.Embedding(vocabulary_size, embedding_size)
        self.linear = nn.Linear(3*embedding_size, vocabulary_size)
        self.linear_matrix_2 = nn.Linear(embedding_size*3, embedding_size*3)
        self.relu = nn.ReLU()
        self.softmax = nn.Softmax()
        self.beta = beta_factor

    def forward(self, x): #x is list of prev and following embeddings
        emb_iminusOne = self.embeddings(x[1])*pow(self.beta, 1) 
        emb_iminusTwo = self.embeddings(x[0])*pow(self.beta, 2)
        emb_bow = self.embeddings(torch.stack((x[2],x[3],x[4]), dim=0)).mean(dim=0)*pow(self.beta, 4) #words w_i-5, w_i-4, w_i-3

        for tensor in [emb_iminusOne, emb_iminusTwo, emb_bow]:
            if tensor.isnan().any():
                    print(tensor)
        #       clamp()
        first_layer_size_2 = self.linear_matrix_2(torch.cat((emb_iminusOne, emb_iminusTwo, emb_bow), dim=1))
        first_relu = self.relu(first_layer_size_2)
        concated = self.linear(first_relu)
        out = concated.clamp(min=1e-4, max=1e4)
        out = self.softmax(concated)
        return out

In [17]:
data = DataLoader(train_dataset, batch_size=params['batch_size'])

In [28]:
next(iter(data))

[tensor([  31,  191, 6017,  ...,    0,    0,   46]),
 tensor([ 191, 6017,    1,  ...,    0,   46, 2607]),
 tensor([6017,    1,  114,  ...,   46, 2607,  115]),
 tensor([   1,  114,  165,  ..., 2607,  115,    4]),
 tensor([  114,   165,     4,  ...,   115,     4, 14165]),
 tensor([  165,     4,    27,  ...,     4, 14165, 18228])]

In [36]:
import gc
torch.cuda.empty_cache()
gc.collect()

0

In [37]:
device = 'cuda'
model = BoW_position_HexagramNeuralLanguageModel(params['vocab_size'], params['embed_size'], params['beta']).to(device)
optimizer = torch.optim.Adam(model.parameters(), lr=params['learning_rate'])
criterion = torch.nn.NLLLoss()
model_state_name = 'model-hexa-bag-following'

In [38]:
print(model)

BoW_position_HexagramNeuralLanguageModel(
  (embeddings): Embedding(35000, 256)
  (linear): Linear(in_features=768, out_features=35000, bias=True)
  (linear_matrix_2): Linear(in_features=768, out_features=768, bias=True)
  (relu): ReLU()
  (softmax): Softmax(dim=None)
)


In [24]:
torch.autograd.set_detect_anomaly(True)
# model.load_state_dict(torch.load(model_state_name + f'-2.bin'))
# for i in range(30):
for i in range(params['epochs']):
    print('epoch: =', i)
    model.train()
    step = 0
    for x_presc_2, x_presc_1, x_pred, xfoll1, xfoll2, xfoll3 in data: # word, following, 2nd_following words
       x_presc_2 = x_presc_2.to(device)
       x_presc_1 = x_presc_1.to(device)
       x_pred = x_pred.to(device)
       xfoll1 = xfoll1.to(device)
       xfoll2 = xfoll2.to(device)
       xfoll3 = xfoll3.to(device)
       optimizer.zero_grad()
       ypredicted = model(torch.stack([x_presc_2, x_presc_1, xfoll1, xfoll2, xfoll3], dim = 0)) #following, 2nd_following word
       loss = criterion(torch.log(ypredicted), x_pred) #x is to_predict
       if(torch.log(ypredicted).isnan().any()):
          print("NAN values in ypredicted")
       if step % 100 == 0:
          print(step, loss)
       step += 1
       if step % 10000 == 0:
           torch.save(model.state_dict(), model_state_name + f'-{step}.bin')
       loss.backward()
       optimizer.step()
    torch.save(model.state_dict(), model_state_name + f'-{i}.bin')    
torch.save(model.state_dict(), model_state_name + f'-final.bin')

epoch: = 0


/tmp/ipykernel_6912/1385550624.py:24: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  out = self.softmax(concated)


0 tensor(10.4859, device='cuda:0', grad_fn=<NllLossBackward0>)
1000
100 tensor(6.4495, device='cuda:0', grad_fn=<NllLossBackward0>)
200 tensor(6.1373, device='cuda:0', grad_fn=<NllLossBackward0>)
2000
300 tensor(6.0952, device='cuda:0', grad_fn=<NllLossBackward0>)
3000
400 tensor(6.0426, device='cuda:0', grad_fn=<NllLossBackward0>)
4000
500 tensor(5.8780, device='cuda:0', grad_fn=<NllLossBackward0>)
5000
600 tensor(5.9308, device='cuda:0', grad_fn=<NllLossBackward0>)
6000
700 tensor(5.8750, device='cuda:0', grad_fn=<NllLossBackward0>)
7000
800 tensor(5.5971, device='cuda:0', grad_fn=<NllLossBackward0>)
8000
900 tensor(5.6050, device='cuda:0', grad_fn=<NllLossBackward0>)
9000
1000 tensor(5.5437, device='cuda:0', grad_fn=<NllLossBackward0>)
10000
1100 tensor(5.6054, device='cuda:0', grad_fn=<NllLossBackward0>)
11000
1200 tensor(5.6719, device='cuda:0', grad_fn=<NllLossBackward0>)
12000
1300 tensor(5.6564, device='cuda:0', grad_fn=<NllLossBackward0>)
13000
1400 tensor(5.7387, device='cuda

/home/gedin/.local/lib/python3.10/site-packages/torch/autograd/__init__.py:200: UserWarning: Error detected in LogBackward0. Traceback of forward call that caused the error:
  File "/usr/lib/python3.10/runpy.py", line 196, in _run_module_as_main
    return _run_code(code, main_globals, None,
  File "/usr/lib/python3.10/runpy.py", line 86, in _run_code
    exec(code, run_globals)
  File "/home/gedin/.local/lib/python3.10/site-packages/ipykernel_launcher.py", line 17, in <module>
    app.launch_new_instance()
  File "/home/gedin/.local/lib/python3.10/site-packages/traitlets/config/application.py", line 1043, in launch_instance
    app.start()
  File "/home/gedin/.local/lib/python3.10/site-packages/ipykernel/kernelapp.py", line 725, in start
    self.io_loop.start()
  File "/home/gedin/.local/lib/python3.10/site-packages/tornado/platform/asyncio.py", line 195, in start
    self.asyncio_loop.run_forever()
  File "/usr/lib/python3.10/asyncio/base_events.py", line 600, in run_forever
    sel

RuntimeError: Function 'LogBackward0' returned nan values in its 0th output.

In [36]:
torch.save(model.state_dict(), model_state_name + f'-bs3200-lr0.001embed256.bin')

In [36]:
print((torch.stack([x_presc_2, x_presc_1, xfoll1, xfoll2, xfoll3], dim = 0) == 0))

tensor([[False,  True, False,  ..., False, False,  True],
        [ True, False, False,  ..., False,  True, False],
        [False, False, False,  ..., False, False, False],
        [False, False, False,  ..., False, False,  True],
        [False, False, False,  ..., False,  True, False]], device='cuda:0')


In [31]:
print(torch.log(ypredicted))

tensor([[ -2.5025,  -6.0652,  -4.0346,  ..., -16.9524, -26.7735, -27.9386],
        [ -2.4854,  -3.0847,  -8.8726,  ..., -18.5785, -19.6871, -25.8460],
        [ -1.2366,  -3.7922,  -7.6996,  ..., -24.7869, -25.6722, -27.8850],
        ...,
        [ -1.1097,  -3.8814,  -3.7208,  ..., -17.6482, -17.6953, -26.8819],
        [ -1.0363,  -4.5648,  -2.8412,  ..., -14.2657, -21.2847, -22.4523],
        [ -1.7532,  -4.9568,  -2.6734,  ..., -21.4232, -28.2665, -28.4816]],
       device='cuda:0', grad_fn=<LogBackward0>)


In [4]:
a = nn.Embedding(100, 3)

In [15]:
model.load_state_dict(torch.load(model_state_name + f'-2.bin'))

<All keys matched successfully>

In [25]:
model.state_dict()

OrderedDict([('embeddings.weight',
              tensor([[ 0.3889, -0.1857, -0.2153,  ..., -0.7755,  0.1490,  0.0721],
                      [-0.4154,  0.9295,  0.2505,  ...,  0.1146, -0.0905, -0.1508],
                      [ 0.1400, -0.0193,  0.4387,  ...,  0.2155,  0.1525,  0.0426],
                      ...,
                      [-1.4852, -1.5178,  0.1190,  ...,  0.6389,  1.7776,  0.5175],
                      [-0.9921,  0.8200,  0.8319,  ..., -1.1706,  0.3248, -0.6838],
                      [-0.0643,  1.3250,  0.4975,  ...,  0.4697, -1.1095,  0.3388]],
                     device='cuda:0')),
             ('linear.weight',
              tensor([[-0.0706, -0.0996, -0.0251,  ..., -0.1125, -0.0438, -0.0334],
                      [ 0.0339,  0.1630,  0.1329,  ..., -0.0550, -0.1837, -0.0659],
                      [ 0.1722, -0.1080, -0.2127,  ..., -0.0168,  0.1584,  0.0217],
                      ...,
                      [-0.0215, -0.1044, -0.2464,  ..., -0.0469, -0.8416, -0.1299],

In [19]:
model.state_dict()['embeddings.weight'].isnan().any()

tensor(False, device='cuda:0')

In [22]:
for entry in model.state_dict():
    print(entry)

embeddings.weight
linear.weight
linear.bias
linear_matrix_2.weight
linear_matrix_2.bias


In [24]:
for entry in model.state_dict():
    if model.state_dict()[entry].isnan().any():
        print(entry)

In [34]:
ixs = torch.tensor([[31], [191], [1], [114], [165]]).to(device)

out = model(ixs)
top = torch.topk(out[0], 10)
top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

/tmp/ipykernel_6912/1385550624.py:24: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  out = self.softmax(concated)


[('to', 4, 0.46012264490127563),
 ('from', 23, 0.20325958728790283),
 ('in', 6, 0.10610334575176239),
 ('at', 14, 0.08032896369695663),
 ('into', 86, 0.015613404102623463),
 ('In', 30, 0.014342560432851315),
 ('on', 16, 0.008756757713854313),
 ('the', 1, 0.006672270596027374),
 ('<unk>', 0, 0.005862860474735498),
 ('out', 63, 0.00491007836535573)]

In [45]:
def get_values_from_model(context: list, model, vocab, k=10):
    words = [vocab.forward([word]) for word in context]
    ixs =  torch.tensor(words).to(device)
    out = model(ixs)
    top = torch.topk(out[0], k)
    top_indices = top.indices.tolist()
    top_probs = top.values.tolist()
    top_words = vocab.lookup_tokens(top_indices)
    return list(zip(top_words, top_probs))

def summarize_probs_unk(dic, const_wildcard=True):
    ''' 
    dic: dictionary of probabilities returned by model 
    returns: tab of probabilities, with <unk> specificly as last element
    '''
    if const_wildcard:  
        if '<unk>' in dic.keys():
            del dic['<unk>']
        probsum = sum(float(val) for key, val in dic.items())
        for key in dic:
            dic[key] = dic[key]/(probsum*(1+params['wildcard_minweight'])) ###leave some space for wildcard
        tab = [(key, val) for key, val in dic.items()]
        tab.append(('<unk>', 1-sum([val for val in dic.values()])))
    elif '<unk>' not in dic.keys():
        tab = [(key, val) for key, val in dic.items()]
        tab.append(('<unk>', 1-sum([val for val in dic.values()])))
    else:
        wildcard_value = dic['<unk>']
        del dic['<unk>']
        probsum = sum([float(val) for key, val in dic.items()])
        for key in dic:
            dic[key] = dic[key]/(probsum+wildcard_value)
        tab = [(key, val) for key, val in dic.items()]
        tab.append(('<unk>', 1-sum([val for val in dic.values()])))
    return tab

def gonito_format(dic, const_wildcard = True):
    tab = summarize_probs_unk(dic=dic, const_wildcard=const_wildcard)
    result = ''
    for element in tab[:-1]:
        result+=str(element[0])+':'+str(element[1])+'\t'
    result += ':'+ str(tab[-1][1]) + '\n'
    return result

In [40]:
model.load_state_dict(torch.load('model-hexa-bag-following-bs3200-lr0.001embed256.bin'))

<All keys matched successfully>

In [48]:
with lzma.open(test_file, 'rt') as file:
    predict_words = []
    results = []
    for line in file:
        line = replace_endline(line) #get only relevant
        line = line.split('\t')[6:]
        left_context = line[0].rstrip().split(" ")[-2:] #two words from the left context
        right_context = line[1].rstrip().split(" ")[:3]
        context = [*left_context, *right_context]
        predict_words.append(context) #get_first_word(split[1cd 
    vocab = train_dataset.vocab
    for context_words in predict_words:
        predicted_distribution = get_values_from_model(context_words, model, vocab, k=10)
        distribution_as_dict = dict(predicted_distribution)
#         print(distribution_as_dict)
        results.append(distribution_as_dict)

/tmp/ipykernel_5410/1385550624.py:24: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  out = self.softmax(concated)


In [49]:
with open(out_file, 'w') as outfile:
    for elem in results:  
        outfile.write(gonito_format(elem, const_wildcard=False))

In [22]:
left_context = ['a','b']#two words from the left context
right_context =['a','b', 'c'] 
context = [*left_context, *right_context]
print(context)

['a', 'b', 'a', 'b', 'c']
